# Experiment Notebook: {Descriptive Experiment Keywords}

# Table of Contents
* [Experiment Summary](#Experiment-Summary)
* [Experiment Assumptions](#Experiment-Assumptions)
* [Experiment Setup](#Experiment-Setup)
* [Analysis 1: ...](#Analysis-1:-...)

# Experiment Summary 

The purpose of this notebook is to...

# Experiment Assumptions

See [assumptions document](../../ASSUMPTIONS.md) for further details.

- The polygn token price trajectory is in linear from $1 to $5
- New supernet adoption is 20 chains per month.
- All the analysis is based on Multi-staking
- Checkpoint gas fee is paid by ether@$1500


# Experiment Setup

We begin with several experiment-notebook-level preparatory setup operations:

* Import relevant dependencies
* Import relevant experiment templates
* Create copies of experiments
* Configure and customize experiments 

Analysis-specific setup operations are handled in their respective notebook sections.

In [1]:
# Import the setup module:
# * sets up the Python path
# * runs shared notebook configuration methods, such as loading IPython modules
import setup

import copy
import logging
import numpy as np
import pandas as pd
import plotly.express as px

import experiments.notebooks.visualizations as visualizations
from experiments.run import run
from experiments.utils import display_code
import model.constants as constants

time: 2.71 s (started: 2023-06-07 17:32:07 +08:00)


In [2]:
# Enable/disable logging
logger = logging.getLogger()
logger.disabled = False

time: 11.4 ms (started: 2023-06-07 17:32:10 +08:00)


In [3]:
# Import experiment templates
import experiments.templates.polygon.yield_analysis as cumulative_yield_analysis

time: 102 ms (started: 2023-06-07 17:32:10 +08:00)


In [4]:
# Inspect experiment template
display_code(cumulative_yield_analysis)

"""
# Cumulative Yield Analysis
"""

import copy

import model.constants as constants
from model.stochastic_processes import create_stochastic_process_realizations
from model.types import Stage
from experiments.default_experiment import experiment


# Make a copy of the default experiment to avoid mutation
experiment = copy.deepcopy(experiment)

DELTA_TIME = constants.epochs_per_day  # epochs per timestep
SIMULATION_TIME_MONTHS = 4  # number of months
TIMESTEPS = constants.epochs_per_month * SIMULATION_TIME_MONTHS // DELTA_TIME

# Generate stochastic process realizations
polygn_price_samples = create_stochastic_process_realizations("polygn_price_samples", timesteps=TIMESTEPS, dt=DELTA_TIME)

PoS_checkpoint_gas_cost = constants.PoS_checkpoint_gas_cost
parameter_overrides = {
    "polygn_price_process": [lambda run, timestep: polygn_price_samples[run - 1][timestep]],
    "Adoption_speed": [20],
    "checkpoint_gas_cost": [0.1 * PoS_checkpoint_gas_cost]
}

# Override default experiment Simulation and System Parameters related to timing
experiment.simulations[0].timesteps = TIMESTEPS
experiment.simulations[0].model.params.update({"dt": [DELTA_TIME]})

# Override default experiment System Parameters
experiment.simulations[0].model.params.update(parameter_overrides)

time: 41.6 ms (started: 2023-06-07 17:32:10 +08:00)


In [5]:
# gas cost comsumption and validator yield analysis with default settings
simulation_2b = copy.deepcopy(cumulative_yield_analysis.experiment.simulations[0])

time: 12 ms (started: 2023-06-07 17:32:10 +08:00)


In [6]:
# simulation_2b.model.initial_state.update({
#     "PUBLIC_CHAINS_CNT": 5,
#     "PRIVATE_CHAINS_CNT": 20,
# })

simulation_2b.model.params.update({"PRIVATE_CHAINS_CNT": [10]})

PoS_checkpoint_gas_cost = constants.PoS_checkpoint_gas_cost
simulation_2b.model.params.update({
    'slashing_fraction': [0.9],
    'checkpoint_gas_cost': [
        1/100 * PoS_checkpoint_gas_cost,
        10/100 * PoS_checkpoint_gas_cost,
        #50/100 * PoS_checkpoint_gas_cost,
        1 * PoS_checkpoint_gas_cost,
        1 * PoS_checkpoint_gas_cost,
    ],
    ' epochs_once_a_checkpoint_submission': [
        1,
        1,
        1,
        5,
    ],
    
})

time: 11 ms (started: 2023-06-07 17:32:10 +08:00)


In [7]:
df_2b, _exceptions = run(simulation_2b)

2023-06-07 17:32:10,460 - root - INFO - Running experiment
2023-06-07 17:32:10,462 - root - INFO - Starting simulation 0 / run 0 / subset 0
3558814399.3474894
[13107972.00496313 58985874.02233408 39323916.01488939 65539860.02481566
 65539860.02481566 39323916.01488939 91755804.03474191 26215944.00992626
 19661958.00744469 58985874.02233408 72093846.02729721 19661958.00744469
 32769930.01240783 45877902.01737095 32769930.01240783 13107972.00496313
 19661958.00744469 52431888.01985252 19661958.00744469 13107972.00496313
 26215944.00992626 26215944.00992626 32769930.01240783 45877902.01737095
 58985874.02233408  6553986.00248156 45877902.01737095 39323916.01488939
 32769930.01240783 52431888.01985252 45877902.01737095 58985874.02233408
 19661958.00744469 32769930.01240783 13107972.00496313 32769930.01240783
 32769930.01240783 39323916.01488939 45877902.01737095 13107972.00496313
 19661958.00744469 52431888.01985252 45877902.01737095 65539860.02481566
 13107972.00496313 32769930.01240783 3

In [8]:
df_2b[['polygn_supply','network_issuance','total_inflation_to_validators',"polygn_staked"]]

polygn_supply  network_issuance  total_inflation_to_validators  \
1     1.000026e+10     260368.427831                   2.603684e+14   
2     1.000052e+10     259853.921061                   2.598539e+14   
3     1.000078e+10     260159.084711                   2.601591e+14   
4     1.000104e+10     260251.976363                   2.602520e+14   
5     1.000130e+10     259787.014519                   2.597870e+14   
..             ...               ...                            ...   
479   1.003022e+10     260873.384089                   2.608734e+14   
480   1.003048e+10     261278.144620                   2.612781e+14   
481   1.003074e+10     260898.779679                   2.608988e+14   
482   1.003100e+10     260980.833851                   2.609808e+14   
483   1.003126e+10     261316.424942                   2.613164e+14   

     polygn_staked  
1     3.558814e+09  
2     3.558814e+09  
3     3.558814e+09  
4     3.558814e+09  
5     3.558814e+09  
..             ...  
479   1.748037e+09  
480   1.748037e+09  
481   1.748037e+09  
482   1.748037e+09  
483   1.748037e+09  

[480 rows x 4 columns]

time: 23.4 ms (started: 2023-06-07 17:32:11 +08:00)


In [9]:
df_2b.tail(1)['timestamp'].values

array(['2023-10-04T17:32:07.641668000'], dtype='datetime64[ns]')

time: 12 ms (started: 2023-06-07 17:32:11 +08:00)


In [10]:
visualizations.plot_yields_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 174 ms (started: 2023-06-07 17:32:11 +08:00)


In [11]:
visualizations.plot_multichain_attack_51_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 56.8 ms (started: 2023-06-07 17:32:11 +08:00)


In [12]:
visualizations.plot_multichain_attack_33_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 58.2 ms (started: 2023-06-07 17:32:11 +08:00)


In [13]:
visualizations.plot_monoply_51_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 55.7 ms (started: 2023-06-07 17:32:11 +08:00)


In [14]:
visualizations.plot_monoply_33_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 57.7 ms (started: 2023-06-07 17:32:11 +08:00)


In [15]:
visualizations.plot_total_top_51_control_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)



time: 57.7 ms (started: 2023-06-07 17:32:11 +08:00)


In [16]:
visualizations.plot_total_top_33_control_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 56 ms (started: 2023-06-07 17:32:11 +08:00)


In [17]:
visualizations.plot_gini_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)



time: 61.9 ms (started: 2023-06-07 17:32:12 +08:00)


In [18]:
visualizations.plot_hhi_per_subset_subplots(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 55.9 ms (started: 2023-06-07 17:32:12 +08:00)


In [19]:
visualizations.plot_slashing_amount_per_subset(
    df_2b,
    scenario_names=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 47.3 ms (started: 2023-06-07 17:32:12 +08:00)


In [20]:
df_2b.query(f"subset == 1")[['polygn_staked','polygn_staked_per_validator']]

polygn_staked                        polygn_staked_per_validator
122   3.558814e+09  [1428344.2241105586, 19046966.39055203, 393239...
123   3.558814e+09  [1428344.2241105586, 19046966.39055203, 393239...
124   3.558814e+09  [1428344.2241105586, 19046966.39055203, 393239...
125   3.558814e+09  [1428344.2241105586, 19046966.39055203, 393239...
126   3.558814e+09  [1428344.2241105586, 19046966.39055203, 393239...
..             ...                                                ...
237   1.748037e+09  [1428344.2241105586, 19046966.39055203, 393239...
238   1.748037e+09  [1428344.2241105586, 19046966.39055203, 393239...
239   1.748037e+09  [1428344.2241105586, 19046966.39055203, 393239...
240   1.748037e+09  [1428344.2241105586, 19046966.39055203, 393239...
241   1.748037e+09  [1428344.2241105586, 19046966.39055203, 393239...

[120 rows x 2 columns]

time: 20.2 ms (started: 2023-06-07 17:32:12 +08:00)


In [21]:
visualizations.plot_validator_checkpoint_costs(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 189 ms (started: 2023-06-07 17:32:12 +08:00)


In [22]:
visualizations.plot_validator_checkpoint_costs_yields(
    df_2b,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 193 ms (started: 2023-06-07 17:32:12 +08:00)


In [23]:


visualizations.plot_token_price(
    df_2b,
)

time: 28.1 ms (started: 2023-06-07 17:32:12 +08:00)


In [24]:
visualizations.plot_yields_per_subset(df_2b, scenario_names={
        0: '21k gas + 225 checkpoints per day', 
        1: '210k gas + 225 checkpoints per day',
        2: '2.1M gas + 225 checkpoints per day', 
        3: '2.1M gas + 45 checkpoints per day'})

time: 59.5 ms (started: 2023-06-07 17:32:12 +08:00)


In [25]:
visualizations.plot_treasury_per_subset(
    df_2b,
    scenario_names=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 39.8 ms (started: 2023-06-07 17:32:12 +08:00)


In [26]:
df_2b.loc[1,["total_online_validator_rewards"]]

total_online_validator_rewards    268778927830890.125
Name: 1, dtype: object

time: 13.5 ms (started: 2023-06-07 17:32:12 +08:00)


In [27]:
# Gas cost analysis when the price is contant at $1.
simulation_2c = copy.deepcopy(cumulative_yield_analysis.experiment.simulations[0])

simulation_2c.model.params.update({"PRIVATE_CHAINS_CNT": [5]})

PoS_checkpoint_gas_cost = constants.PoS_checkpoint_gas_cost
simulation_2c.model.params.update({
    'polygn_price_process':[
        lambda _run, _timestep: 1,
    ],
    'checkpoint_gas_cost': [
        1/100 * PoS_checkpoint_gas_cost,
        10/100 * PoS_checkpoint_gas_cost,
        #50/100 * PoS_checkpoint_gas_cost,
        1 * PoS_checkpoint_gas_cost,
        1 * PoS_checkpoint_gas_cost,
    ],
    ' epochs_once_a_checkpoint_submission': [
        1,
        1,
        1,
        5,
    ],
    
})

df_2c, _exceptions = run(simulation_2c)

2023-06-07 17:32:12,917 - root - INFO - Running experiment
2023-06-07 17:32:12,918 - root - INFO - Starting simulation 0 / run 0 / subset 0
3558814399.3474894
[ 8741476.53275533 33656726.71827158 16082129.61688449 45245881.28420377
 43706300.66010439 27363409.66640411 60937468.06762111 17742564.685197
 10312514.71442623 48291111.99194416 44022801.85783631 13307256.23047492
 20386192.53555452 26160647.97278852 19412338.05245745  9684635.36081858
 12077079.54522843 42372940.82533152 14058959.23919401 12302088.57484848
 11156355.93837346 14563156.07692871 24266696.39474399 26899245.04983639
 19593222.11093991  3869290.95899853 27143125.42695928 23857283.840461
 25612451.75210138 34971143.76662673 21547579.38145798 25558474.83007102
 15003996.57789001 11886537.50979707  7492499.5787447  18623446.53851248
 27906119.35739168 27607317.50230274 38269585.15995643  8916006.58832074
 10728302.60486061 37170971.73600499 34573769.89746075 41519030.36009353
  5529450.65231452 26310158.61705039 21138

In [28]:
visualizations.plot_yields_per_subset_subplots(
    df_2c,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 93.1 ms (started: 2023-06-07 17:32:13 +08:00)


In [29]:
visualizations.plot_validator_checkpoint_costs(
    df_2c,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 192 ms (started: 2023-06-07 17:32:13 +08:00)


In [30]:
visualizations.plot_validator_checkpoint_costs_yields(
    df_2c,
    subplot_titles=['21k gas + 225 checkpoints per day', 
                    '210k gas + 225 checkpoints per day', 
                    '2.1m gas + 225 checkpoints per day', 
                    '2.1m gas + 45 checkpoints per day']
)

time: 185 ms (started: 2023-06-07 17:32:14 +08:00)


In [31]:
visualizations.plot_token_price(
    df_2c,
)

time: 28.8 ms (started: 2023-06-07 17:32:14 +08:00)


In [32]:
# gas cost comsumption and validator yield analysis
simulation_3 = copy.deepcopy(cumulative_yield_analysis.experiment.simulations[0])

time: 12.3 ms (started: 2023-06-07 17:32:14 +08:00)


In [33]:
simulation_3.model.params.update({"PRIVATE_CHAINS_CNT": [5]})

simulation_3.model.params.update({
    'Adoption_speed': [
        10,
        20,
        30,
    ],
    
})
df_3, _exceptions = run(simulation_3)

2023-06-07 17:32:14,365 - root - INFO - Running experiment
2023-06-07 17:32:14,366 - root - INFO - Starting simulation 0 / run 0 / subset 0
3558814399.3474894
[ 8741476.53275533 33656726.71827158 16082129.61688449 45245881.28420377
 43706300.66010439 27363409.66640411 60937468.06762111 17742564.685197
 10312514.71442623 48291111.99194416 44022801.85783631 13307256.23047492
 20386192.53555452 26160647.97278852 19412338.05245745  9684635.36081858
 12077079.54522843 42372940.82533152 14058959.23919401 12302088.57484848
 11156355.93837346 14563156.07692871 24266696.39474399 26899245.04983639
 19593222.11093991  3869290.95899853 27143125.42695928 23857283.840461
 25612451.75210138 34971143.76662673 21547579.38145798 25558474.83007102
 15003996.57789001 11886537.50979707  7492499.5787447  18623446.53851248
 27906119.35739168 27607317.50230274 38269585.15995643  8916006.58832074
 10728302.60486061 37170971.73600499 34573769.89746075 41519030.36009353
  5529450.65231452 26310158.61705039 21138

In [34]:
visualizations.plot_yields_per_subset_subplots(
    df_3,
    subplot_titles=['Low adoption', 'Median adoption', 'High adoption']
)

time: 68.3 ms (started: 2023-06-07 17:32:15 +08:00)


In [35]:
visualizations.plot_number_of_validators_per_subset(df_3, scenario_names={0: "Low Adoption", 1: "Median Adoption", 2: "High Adoption"})

time: 26.4 ms (started: 2023-06-07 17:32:15 +08:00)


In [36]:
df_3[["number_of_active_validators"]]

number_of_active_validators
1                            100
2                            100
3                            100
4                            100
5                            100
..                           ...
358                          100
359                          100
360                          100
361                          100
362                          100

[360 rows x 1 columns]

time: 14 ms (started: 2023-06-07 17:32:15 +08:00)


In [37]:
visualizations.plot_treasury_per_subset(
    df_3,
    scenario_names=['Low adoption', 'Median adoption', 'High adoption']
)

time: 32.1 ms (started: 2023-06-07 17:32:15 +08:00)
